In [1]:
import plotly.graph_objects as go

from black_76 import *

In [2]:
# 这里定价模型做了改造，兼容到期日的计算
def calculate_option_pnl(
    s: float,
    k: float,
    r: float,
    t: float,
    v: float,
    cp: int,
    price: float
) -> float:
    """计算单一期权到期盈亏"""
    p: float = calculate_price(s, k, r, t, v, cp)
    return p - price

In [3]:
# legs中的每个元素为字典，具体键包括k、cp、price、pos
def calculate_spread_pnl(
    s: float,
    r: float,
    t: float,
    v: float,
    legs: list
) -> float:
    """计算期权价差权到期盈亏"""
    pnl: float = 0

    for leg in legs:
        p: float = calculate_price(s, leg["k"], r, t, v, leg["cp"])
        pnl += (p - leg["price"]) * leg["pos"]

    return pnl

In [4]:
def plot_option_spread(
    underlying_prices: list[float],
    r: float,
    t: float,
    v: float,
    legs: list
):
    results: dict = {}

    for s in underlying_prices:
        pnl: float = calculate_spread_pnl(s, r, t, v, legs)
        results[s] = pnl

    fig = go.Figure(data=go.Scatter(x=list(results.keys()), y=list(results.values())))
    fig.show()

    return results

In [12]:
def calculate_option_spread(
    underlying_prices: list[float],
    r: float,
    t: float,
    v: float,
    legs: list
) -> list[float]:
    results: dict = {}

    for s in underlying_prices:
        pnl: float = calculate_spread_pnl(s, r, t, v, legs)
        results[s] = pnl

    return results

In [26]:
# 定价参数
underlying_prices = range(2500, 3550, 50)
option_strike = 3000
discount_rate = 0.03
expiry_time = 0             # 到期日当天
pricing_volatility = 0.2
option_type = 1
option_price = 70

In [27]:
# 跨式价差
legs = [
    {
        "k": 3000,
        "cp": 1,
        "price": 70,
        "pos": 1
    },
    {
        "k": 3000,
        "cp": -1,
        "price": 70,
        "pos": 1
    }
]

In [14]:
# 牛市价差
legs = [
    {
        "k": 3000,
        "cp": 1,
        "price": 70,
        "pos": 1
    },
    {
        "k": 3200,
        "cp": 1,
        "price": 30,
        "pos": -1
    }

]

In [28]:
# 绘制不同剩余到期时间下的价差盈亏曲线
fig = go.Figure()

for days in range(0, 30, 5):
    t: float = days / 240
    results = calculate_option_spread(underlying_prices, discount_rate, t, pricing_volatility, legs)
    fig.add_trace(go.Scatter(x=list(results.keys()), y=list(results.values()), name=f"days={days}"))

fig.show()